Say you have a bag of 99 fair coins and 1 coin that has heads on both sides.  You draw a coin from the bag and flip it 10 times, each time showing heads.  What is the probability you drew the unfair coin?

# Analytic Solution
We want to know the probability the coin drawn from the bag was the unfair coin, given it flipped heads 10 times.  

---
## Conditional Probability
To solve this analytically, first we need to learn about conditional probability.  Consider two events we will represent using $A$ and $B$.  For our example, the events will be:   

        A) drawing the unfair coin from the bag    
        B) flipping heads 10 times 

The probability of both events happening, $P(A\cap B)$, is equal to the probability of $A$ happening, $P(A)$, multiplied by the probability of $B$ happening given $A$ has occurred, $P(B|A)$.  

$$P(A\cap B) = P(B|A) P(A)$$

We could also switch this around, as $P(A\cap B)$ also is equal to the probability of $B$ happening, $P(B)$, multiplied by the probability of $A$ happening given $B$ has occurred, $P(A|B)$.

$$P(A\cap B) = P(A|B) P(B)$$

Putting these equalities together, we have 
$$P(A|B) P(B) = P(B|A) P(A)$$

which we can rewrite as
$$ P(A | B) = \frac{P(B | A) P(A)}{P(B)} $$

This is Bayes' theorem.

---
## What about the coin you drew?
To figure out the probability you drew the unfair coin, we have
- the probability of drawing the unfair coin from the bag: $P(A)$
- the probability of flipping heads 10 times: $P(B)$

We know the probability of drawing the unfair coin.
$$P(A) = 1 / 100$$

If we did draw the unfair coin, we know the probability of flipping heads 10 times will be

$$P(B | A) = 10 / 10 = 1$$

What about the probabilities related to drawing a fair coin, or not drawing the unfair coin, $P(!A)$?  The probability of not drawing the fair coin is $1 - P(A)$, or

$$P(!A) = 99 / 100$$

If we did draw a fair coin, we know the probability of flipping heads will be 1/2 for each flip, so for 10 flips we get

$$P(B | !A) = 1/2^{10}$$

From this we can calculate the probability of flipping nheads 10 times, $P(B)$, as

$$P(B) = P(B | A) P(A) + P(B | !A) P(!A)$$

or 

$$P(B) = 1 \times 1/100 + 1/2^{10} \times 99/100$$

and we have everything we need to solve the problem.

In [1]:
p_a = 1.0 / 100.0
p_ba = 1.0
p_na = 99.0 / 100.0
p_bna = 0.5 ** 10

p_b = p_ba * p_a + p_bna * p_na
p_ab = p_ba * p_a / p_b

print(f'Probability the drawn coin was unfair, given it flipped heads 10 times: {p_ab:0.3}')

Probability the drawn coin was unfair, given it flipped heads 10 times: 0.912


So the coin you drew is 91% likely to be the unfair coin.  **Is that as lower/higher than you thought?**

# Calculated Solution
Lets apply our Python hacking skills to instead simulate the experiment and see how often flipping 10 heads resulted from the unfair coin.

In [63]:
import numpy as np
np.set_printoptions(suppress=True)
from numpy.random import RandomState

In [42]:
prng = RandomState(1234)

Setup the coins:

In [3]:
# 100 coin all fair
n_coins = 100
coins = np.zeros(n_coins, dtype=np.int)  

# make one random coin unfair
coins[np.random.randint(1, n_coins, 1)] = 1

Define the coin draw-flip routine:

In [49]:
def draw_coin_and_flip(n_repeats, coins, *, n_flips=10):
    all_heads = []
    n_coins = len(coins)
    
    for i in range(n_repeats):
        coin_index = np.random.randint(0, n_coins, 1)[0]
        drawn_coin = coins[coin_index]
        coin_unfair = drawn_coin == 1  # did we get the unfair coin?
        
        for j in range(n_flips):
            flip = np.random.rand()  # random number between [0, 1)
            
            if coin_unfair or flip < 0.5:
                heads = True
            else:
                heads = False
                break
        
        if heads:
            # store the index and if the coin was unfair
            all_heads.append([i, coin_unfair])  
    
    return all_heads

Simulate the coin draw-flip routine a million times.

In [50]:
n_repeats = int(1e6)
first_million = draw_coin_and_flip(n_repeats, coins, n_flips=10)

In [120]:
def fraction_all_heads_unfair(all_heads_coins):
    for i in range(n_all_heads):
        i1 = i + 1
        all_heads_coins[i, 2] = all_heads_coins[:i1, 1].sum() / i1

In [121]:
# evaluate the results
n_all_heads = len(first_million)
print(f'Of {n_repeats} repeated tests, {n_all_heads} showed heads 10 times')

all_heads_coins = np.c_[np.array(first_million), np.empty(n_all_heads)]
fraction_all_heads_unfair(all_heads_coins)
print(f'probability coin was unfair: {all_heads_coins[-1, 2]:.04}')

Of 1000000 repeated tests, 10972 showed heads 10 times
probability coin was unfair: 0.9105


**This is the same probability we got from the analytic solution.**  Lets see how this changed over the course of the simulation.

In [108]:
import bokeh.plotting
from bokeh.palettes import Category10_10 as palette

In [86]:
import bokeh.resources
bokeh.plotting.output_notebook(resources=bokeh.resources.INLINE)

Loading BokehJS ...

In [88]:
p = bokeh.plotting.figure(width=400, height=400,
    y_axis_label='fraction of times 10 heads was from the unfair coin',
    x_axis_label='trials (e6)')

p.line(all_heads_coins[:, 0]/n_repeats, all_heads_coins[:, 2], 
       color=palette[0], legend='simulated result')
p.line(all_heads_coins[[0, -1], 0]/n_repeats, [p_ab, p_ab], 
       color=palette[1], legend='analytic result')

p.legend.location = 'top_right'
bokeh.plotting.show(p)

We see the simulated result equilibrated rather quickly to a value close to the analytic result.  We expect that running for a longer number of iterations would further improve the agreement.

Lets run for another million steps, then combine the results.

In [91]:
nine_million = draw_coin_and_flip(int(9e6), coins, n_flips=10)

In [113]:
nine_million = np.array(nine_million)
nine_million[:, 0] += int(1e6)

In [115]:
# combine the results
ten_million = np.r_[first_million, nine_million]

In [122]:
# evaluate the results
n_all_heads = len(ten_million)
print(f'Of {n_repeats*10} repeated tests, {n_all_heads} showed heads 10 times.')

all_heads_coins = np.c_[np.array(ten_million), np.empty(n_all_heads)]
fraction_all_heads_unfair(all_heads_coins)
print(f'Of those {n_all_heads} all heads runs, {all_heads_coins[-1, 2]*100:0.3}% were the unfair coin') 

Of 10000000 repeated tests, 109706 showed heads 10 times.
Of those 109706 all heads runs, 91.3% were the unfair coin


This matches the analytic result.  There is a small difference of 0.1%, which likely indicates the system has not fully equilibrated.  Regardless, we were able to use the computer to get the result without using statistics by quickly simulate lots of trials the same result.

In [129]:
n_repeats

1000000

In [132]:
p = bokeh.plotting.figure(width=400, height=400,
    y_axis_label='fraction of times 10 heads was from the unfair coin',
    x_axis_label='trials/1,000,000')

p.line(all_heads_coins[:, 0]/n_repeats, all_heads_coins[:, 2], 
       color=palette[0], legend='simulated result')
p.line(all_heads_coins[[0, -1], 0]/n_repeats, [p_ab, p_ab], 
       color=palette[1], legend='analytic result')

p.legend.location = 'top_right'
bokeh.plotting.show(p)

Lets setup a more granular simulation, with a plot that updates as we draw coins and flip them.

In [145]:
for j in range(2):
    for i in range(10):
        print(i)
        if i < 3:
            heads = True
        else:
            heads = False
            break
        print(heads)

0
True
1
True
2
True
3
0
True
1
True
2
True
3


In [146]:
%%timeit 
for j in range(10):
    flip = np.random.rand()
    if flip < 0.5:
        all_heads = True
    else:
        all_heads = False
        break

1.44 µs ± 19.6 ns per loop (mean ± std. dev. of 7 runs, 1000000 loops each)


In [147]:
flip = np.random.rand(10)

In [150]:
np.alltrue(flip < 0.5)

False

In [151]:
%%timeit
flips = np.random.rand(10)
if np.alltrue(flips < 0.5):
    all_heads = True
else:
    all_heads = False

5.6 µs ± 354 ns per loop (mean ± std. dev. of 7 runs, 100000 loops each)


In [155]:
def flip_generator(n_repeats, coins, *, n_flips=10):
    n_coins = len(coins)
    
    for i in range(n_repeats):
        coin_index = np.random.randint(0, n_coins, 1)[0]
        drawn_coin = coins[coin_index]
        coin_unfair = drawn_coin == 1  # did we get the unfair coin?
        
        if coin_unfair:
            all_heads = True
        else: 
            for j in range(n_flips):
                flip = np.random.rand()  # random number between [0, 1)

                if flip < 0.5:
                    all_heads = True
                else:
                    all_heads = False
                    break

        if all_heads:
            # report the index and if the coin was unfair
            yield i, coin_unfair

In [157]:
for res in flip_generator(10000, coins):
    print(res)

(69, True)
(125, False)
(314, True)
(330, True)
(334, True)
(444, True)
(567, True)
(580, True)
(730, True)
(865, True)
(1046, True)
(1090, True)
(1107, True)
(1242, True)
(1386, True)
(1503, False)
(1671, True)
(1811, True)
(1961, True)
(2080, True)
(2088, True)
(2238, True)
(2247, True)
(2416, True)
(2524, True)
(2878, True)
(3149, True)
(3179, False)
(3183, True)
(3235, True)
(3293, True)
(3361, True)
(3400, True)
(3407, True)
(3471, True)
(3708, True)
(3893, True)
(4027, False)
(4162, True)
(4387, True)
(4536, True)
(4582, True)
(4649, True)
(4901, True)
(5181, False)
(5315, True)
(5360, False)
(5380, True)
(5542, True)
(5614, True)
(6027, True)
(6053, True)
(6083, True)
(6208, True)
(6297, True)
(6438, True)
(6461, False)
(6499, True)
(6518, True)
(6561, True)
(6773, True)
(6917, True)
(7037, True)
(7097, True)
(7319, True)
(7322, True)
(7334, True)
(7528, True)
(7547, True)
(7558, True)
(7583, True)
(7588, True)
(7615, True)
(7639, False)
(7727, True)
(7736, True)
(7752, True)
(7

In [138]:
draw_coin_and_flip(1, coins, n_flips=10)

[]

In [136]:
my_fig = bokeh.plotting.figure(
    width=400, height=400,
    y_axis_label='fraction of times 10 heads was from the unfair coin',
    x_axis_label='trials/1,000,000',    
)

frac_unfair = bokeh.models.sources.ColumnDataSource(data=dict(x=[], y=[]))

circle1 = my_fig.line(
    "x", "y", 
    source=frac_unfair,
    color=palette[0],
)

handle = bokeh.io.show(my_fig, notebook_handle=True)

new_frac_unfair=dict(x=[], y=[])

step = 0
max_step = int(10e6)  # arbitrary stop point for example

while step < max_step:
    new_frac_unfair['x'] = [np.random.normal(loc=mu_x1, scale=sigma_x1)]
    new_frac_unfair['y'] = [np.random.normal(loc=mu_y1, scale=sigma_y1)]
    
    frac_unfair.stream(new_frac_unfair)
    
    bokeh.io.push_notebook(handle=handle)
    step += 1

NameError: name 'mu_x1' is not defined